In [6]:
!pip install einops

In [3]:
!pip install icecream

In [4]:
!pip install modelscope

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.9/5.9 MB 35.6 MB/s eta 0:00:00


In [3]:
import json
import os
import pandas as pd

# Set display option for long text if needed
pd.set_option('display.max_colwidth', None)

# Load annotation data from JSON
with open('Annotations/val_v1.0_withQT.json') as f:
    data = json.load(f)

# Create a DataFrame from the annotations data.
df = pd.DataFrame(data['data'])

# Define the directory where the images are stored.
# Adjust the path if needed.
image_dir = "/home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/"

# Create a new column "image" that stores the full path to the image.
# This assumes your image files follow the naming pattern: 
# document_id + "_" + document_page_no + ".jpg"
def extract_image_path(row):
    filename = row['ucsf_document_id'] + "_" + row['ucsf_document_page_no'] + ".png"
    return os.path.join(image_dir, filename)

df['image'] = df.apply(extract_image_path, axis=1)

# Now display only the image path, question, and answers.
display(df[["image", "question", "answers"]].head(2))


image  \
0  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/pybv0228_81.png   
1   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   

                                                     question  \
0  What is the ‘actual’ value per 1000, during the year 1975?   
1                                 What is name of university?   

                                                                                     answers  
0                                                                                     [0.28]  
1  [university of california, University of California, university of california, san diego]

In [2]:
import torch
import gc

# Delete the model
# del model
# del tokenizer

# Clear GPU cache
torch.cuda.empty_cache()

# Run garbage collection
gc.collect()

571

using VLM zero shot learning

In [ ]:
import torch
from transformers import AutoConfig, AutoModel
# model_path = 'mPLUG/mPLUG-Owl3-7B-240728'# 64.78%
model_path = 'mPLUG/mPLUG-Owl3-7B-241101'# 63.91%
config = AutoConfig.from_pretrained(model_path, trust_remote_code=True)
print(config)
# model = mPLUGOwl3Model(config).cuda().half()
model = AutoModel.from_pretrained(model_path, attn_implementation='sdpa', torch_dtype=torch.half, trust_remote_code=True)
model.eval().cuda()

mPLUGOwl3Config {
  "_name_or_path": "mPLUG/mPLUG-Owl3-7B-241101",
  "architectures": [
    "mPLUGOwl3Model"
  ],
  "attention_dropout": 0.0,
  "auto_map": {
    "AutoConfig": "mPLUG/mPLUG-Owl3-7B-241101--configuration_mplugowl3.mPLUGOwl3Config",
    "AutoModel": "mPLUG/mPLUG-Owl3-7B-241101--modeling_mplugowl3.mPLUGOwl3Model",
    "AutoModelForCausalLM": "mPLUG/mPLUG-Owl3-7B-241101--modeling_mplugowl3.mPLUGOwl3Model"
  },
  "bos_token_id": 151643,
  "eos_token_id": 151645,
  "hidden_act": "silu",
  "hidden_size": 3584,
  "hyper_layers": [
    7,
    15,
    23,
    26
  ],
  "image_size": 378,
  "initializer_range": 0.02,
  "intermediate_size": 18944,
  "max_position_embeddings": 32768,
  "max_window_layers": 28,
  "model_type": "mplugowl3",
  "num_attention_heads": 28,
  "num_hidden_layers": 28,
  "num_key_value_heads": 4,
  "patch_size": 14,
  "rms_norm_eps": 1e-06,
  "rope_scaling": null,
  "rope_theta": 1000000.0,
  "sliding_window": null,
  "tie_word_embeddings": false,
  "torch_d

/home/cheng-ubuntu/anaconda3/envs/torch180/lib/python3.13/site-packages/transformers/models/auto/image_processing_auto.py:524: FutureWarning: The image_processor_class argument is deprecated and will be removed in v4.42. Please use `slow_image_processor_class`, or `fast_image_processor_class` instead
  warnings.warn(


import flash_attn rotary fail


HyperQwen2ForCausalLM has generative capabilities, as `prepare_inputs_for_generation` is explicitly overwritten. However, it doesn't directly inherit from `GenerationMixin`. From 👉v4.50👈 onwards, `PreTrainedModel` will NOT inherit from `GenerationMixin`, and this model will lose the ability to call `generate` and other related functions.
  - If you're using `trust_remote_code=True`, you can get rid of this warning by loading the model with an auto class. See https://huggingface.co/docs/transformers/en/model_doc/auto#auto-classes
  - If you are the owner of the model architecture code, please modify your model class such that it inherits from `GenerationMixin` (after `PreTrainedModel`, otherwise you'll get an exception).
  - If you are not the owner of the model architecture class, please contact the model code owner to update it.


mPLUGOwl3Model(
  (vision_model): SiglipVisionTransformer(
    (embeddings): SiglipVisionEmbeddings(
      (patch_embedding): Conv2d(3, 1152, kernel_size=(14, 14), stride=(14, 14), padding=valid)
      (position_embedding): Embedding(729, 1152)
    )
    (encoder): SiglipEncoder(
      (layers): ModuleList(
        (0-26): 27 x SiglipEncoderLayer(
          (self_attn): SiglipAttention(
            (k_proj): Linear(in_features=1152, out_features=1152, bias=True)
            (v_proj): Linear(in_features=1152, out_features=1152, bias=True)
            (q_proj): Linear(in_features=1152, out_features=1152, bias=True)
            (out_proj): Linear(in_features=1152, out_features=1152, bias=True)
          )
          (layer_norm1): LayerNorm((1152,), eps=1e-06, elementwise_affine=True)
          (mlp): SiglipMLP(
            (activation_fn): PytorchGELUTanh()
            (fc1): Linear(in_features=1152, out_features=4304, bias=True)
            (fc2): Linear(in_features=4304, out_features=11

In [5]:
from transformers import AutoTokenizer

# Load the tokenizer.
tokenizer = AutoTokenizer.from_pretrained(model_path)

# Initialize the processor using the model method.
# The processor is responsible for handling both the image and text inputs.
processor = model.init_processor(tokenizer)

tokenizer_config.json:   0%|          | 0.00/1.29k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/2.78M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/1.67M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/7.03M [00:00<?, ?B/s]

In [6]:
import transformers
print(transformers.__version__)

4.47.1


In [7]:
# 3. Apply the Model on Each DocVQA Example
# ---------------------------
# Loop through the DataFrame rows, processing each image and its associated question.
from PIL import Image

generated_answers = [] 
for idx, row in df.iterrows():
    image_path = row['image']
    question = row['question']
    gt_answer = row['answers']  # Ground truth answer (for reference/comparison)

    # Load the image from disk.
    try:
        image = Image.open(image_path).convert("RGB")
        # image = Image.new('RGB', (500, 500), color='red')
    except Exception as e:
        print(f"Error loading image {image_path}: {e}")
        continue
    
    # Construct the input messages.
    # Here the prompt is built using the special token <|image|> that mPLUG expects,
    # followed by your question. The second message is left empty for the assistant.
    messages = [
        {"role": "user", "content": f"""<|image|>
    Can you answer this question?{question}"""},
        {"role": "assistant", "content": ""}
    ]

    # Use the processor to convert messages and images to model inputs.
    inputs = processor(messages, images=[image], videos=None)
    # Debug: print input shapes and media_offset
    # print("input_ids shape:", inputs.input_ids.shape)
    # if "media_offset" in inputs:
    #     print("media_offset:", inputs.media_offset)

    # Move inputs to GPU.
    inputs.to('cuda')
    
    # --- Workaround: force all begin indices in media_offset to zero ---
    # if "media_offset" in inputs and inputs["media_offset"].ndim == 3:
    #     inputs["media_offset"][:, :, 0] = 0
    #     print("After override, media_offset:", inputs.media_offset)
    
    
    # Add additional parameters required for generation.
    inputs.update({
        'tokenizer': tokenizer,
        'max_new_tokens': 100,  # you can adjust as needed
        'decode_text': True#,    # instructs the processor to decode generated tokens into text
        # 'stream': False,  # force non-streaming mode
        # 'use_cache': False  # disable cache-based optimizations
    })
    
    
    # The output is assumed to be a list; here we get the first result.
    answer = model.generate(**inputs)
    generated_answers.append(answer)
    # Display the result.
    print("--------------------------------------------------")
    print(f"Image: {image_path}")
    print(f"Question: {question}")
    print(f"Generated Answer: {answer}")
    print(f"Ground Truth Answer: {gt_answer}")
    print("--------------------------------------------------\n")

# Add the new column to the DataFrame
df['generated_answer'] = generated_answers

# Optionally, save the DataFrame to a CSV file for later use
# df.to_csv('docvqa_generated_answers.csv', index=False)
display(df.head(5))

The `seen_tokens` attribute is deprecated and will be removed in v4.41. Use the `cache_position` model input instead.
`get_max_cache()` is deprecated for all Cache classes. Use `get_max_cache_shape()` instead. Calling `get_max_cache()` will raise error from v4.48
The attention layers in this model are transitioning from computing the RoPE embeddings internally through `position_ids` (2D tensor with the indexes of the tokens), to using externally computed `position_embeddings` (Tuple of tensors, containing cos and sin). In v4.46 `position_ids` will be removed and `position_embeddings` will be mandatory.


tensor([[    23,     13,     17,     19, 151645]], device='cuda:0')
--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/pybv0228_81.png
Question: What is the ‘actual’ value per 1000, during the year 1975?
Generated Answer: ['8.24']
Ground Truth Answer: ['0.28']
--------------------------------------------------

tensor([[   359,   2977,    315,  78857, 151645]], device='cuda:0')
--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png
Question: What is name of university?
Generated Answer: ['university of california']
Ground Truth Answer: ['university of california', 'University of California', 'university of california, san diego']
--------------------------------------------------

tensor([[   952,     34, 151645]], device='cuda:0')
--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/pr

questionId                                                    question  \
0       49153  What is the ‘actual’ value per 1000, during the year 1975?   
1       24580                                 What is name of university?   
2       57349                            What is the name of the company?   
3       24581                           Where is the university located ?   
4       24582                               To whom is the document sent?   

        question_types  \
0     [figure/diagram]   
1             [others]   
2             [layout]   
3             [others]   
4  [handwritten, form]   

                                                                                 image  \
0  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/pybv0228_81.png   
1   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   
2  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_22.png   
3   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   
4   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   

   docId ucsf_document_id ucsf_document_page_no  \
0  14465         pybv0228                    81   
1   7027         nkbl0226                     1   
2   4733         snbx0223                    22   
3   7027         nkbl0226                     1   
4   7027         nkbl0226                     1   

                                                                                     answers  \
0                                                                                     [0.28]   
1  [university of california, University of California, university of california, san diego]   
2                                                                 [itc limited, ITC Limited]   
3                                                                     [san diego, San Diego]   
4                                                                                     [Paul]   

  data_split            generated_answer  
0        val                      [8.24]  
1        val  [university of california]  
2        val                       [ITC]  
3        val                 [San Diego]  
4        val                [Ms. Wilson]

In [8]:
import Levenshtein

def normalized_levenshtein_similarity(s1, s2):
    # If the input is a list, join its elements into a string.
    if isinstance(s1, list):
        s1 = " ".join(map(str, s1))
    if isinstance(s2, list):
        s2 = " ".join(map(str, s2))
        
    # Convert to string, lowercase, and remove surrounding whitespace.
    s1 = str(s1).lower().strip()
    s2 = str(s2).lower().strip()
    
    dist = Levenshtein.distance(s1, s2)
    max_len = max(len(s1), len(s2))
    if max_len == 0:
        return 1.0
    return 1 - (dist / max_len)

# Function to compute the similarity for a single row
def row_similarity(row):
    # Assume row['answers'] is a list of ground-truth strings
    ground_truths = row['answers']
    generated = row['generated_answer']
    # Compute similarity with each ground truth answer
    similarities = [normalized_levenshtein_similarity(gt, generated) for gt in ground_truths]
    # We take the maximum similarity (best match) as the score for that row.
    return max(similarities) if similarities else 0.0


# Compute similarity for each row
df["similarity"] = df.apply(row_similarity, axis=1)

# Calculate the average similarity (ANSL)
ansl_accuracy = df["similarity"].mean()

print("Row similarities:")
print(df[["answers", "generated_answer", "similarity"]])
print("Average Normalized Levenshtein Similarity (ANSL):", ansl_accuracy)

Row similarities:
                                                                                                                        answers  \
0                                                                                                                        [0.28]   
1                                     [university of california, University of California, university of california, san diego]   
2                                                                                                    [itc limited, ITC Limited]   
3                                                                                                        [san diego, San Diego]   
4                                                                                                                        [Paul]   
...                                                                                                                         ...   
5344                                                             

In [9]:
df[df["similarity"]<0.5].head(20)

questionId  \
2        57349   
4        24582   
8        49168   
9        24423   
11       57364   
12       57366   
15       57370   
16       57371   
17       57372   
19       57373   
22       57376   
30       57391   
34       57402   
38       57407   
39       16447   
40       57409   
44       57413   
45       57414   
46       57415   
47       57416   

                                                                                                  question  \
2                                                                         What is the name of the company?   
4                                                                            To whom is the document sent?   
8                                                                         What time is the ‘coffee break’?   
9                             According to budget request summary what is total amount of other expenses??   
11                                                         What is the name of the choco fills advertised?   
12                                                 What is the name of the fashion wear/clothing advertise   
15                                        How many nomination committee meetings has S. Banerjee attended?   
16  What is the 'no. of persons present' for the sustainability committee meeting held on 5th April, 2012?   
17        What is the committee strength for the sustainability committee meeting held on 5th April, 2012?   
19                                How many sustainability committee meetings has Y. C. Deveshwar attended?   
22                                             What is the % of raw material imported in the current year?   
30                                                                        What is the name of the company?   
34                                             Who was the director having the highest number of options ?   
38                                                    What is the no. of Ordinary shares held by N. Anand?   
39             What percentage of non-smokers feel the need to restore romance and mystery to modern life?   
40                                                                        What is the name of the company?   
44                                                     Name the 4 significant personal care brands of ITC?   
45                                                    What are the 2 educational/stationary brands of ITC?   
46                                                       What are the 2 lifestyle & apparel brands of ITC?   
47                                                            What is the name of the ITC Agarbatti brand?   

         question_types  \
2              [layout]   
4   [handwritten, form]   
8          [table/list]   
9    [form, table/list]   
11        [Image/Photo]   
12        [Image/Photo]   
15         [table/list]   
16         [table/list]   
17         [table/list]   
19         [table/list]   
22               [form]   
30             [layout]   
34         [table/list]   
38         [table/list]   
39         [table/list]   
40             [layout]   
44          [free_text]   
45          [free_text]   
46          [free_text]   
47          [free_text]   

                                                                                  image  \
2   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_22.png   
4    /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   
8   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/txpp0227_10.png   
9   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/zxfk0226_13.png   
11  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_22.png   
12  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_22.png   
15  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_44.png   
16  /home/cheng-ub

In [16]:
print(len(df))

5349


Using Llava

In [4]:
import torch
from transformers import AutoProcessor, LlavaForConditionalGeneration, AutoModelForImageTextToText

model_id = "llava-hf/llava-1.5-7b-hf"

processor = AutoProcessor.from_pretrained(model_id)
model = AutoModelForImageTextToText.from_pretrained(model_id, torch_dtype=torch.float16).to(0)

processor_config.json:   0%|          | 0.00/173 [00:00<?, ?B/s]

chat_template.json:   0%|          | 0.00/701 [00:00<?, ?B/s]

preprocessor_config.json:   0%|          | 0.00/505 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.45k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

...

model-00001-of-00003.safetensors:   0%|          | 0.00/4.99G [00:00<?, ?B/s]

model-00002-of-00003.safetensors:   0%|          | 0.00/4.96G [00:00<?, ?B/s]

model-00003-of-00003.safetensors:   0%|          | 0.00/4.18G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/141 [00:00<?, ?B/s]

In [5]:
processor = AutoProcessor.from_pretrained(model_id)

In [11]:
# 3. Apply the Model on Each DocVQA Example
# ---------------------------
# Loop through the DataFrame rows, processing each image and its associated question.
from PIL import Image

generated_answers = [] 
for idx, row in df.iterrows():
    image_path = row['image']
    question = row['question']
    gt_answer = row['answers']  # Ground truth answer (for reference/comparison)

    # Load the image from disk.
    try:
        image = Image.open(image_path).convert("RGB")
        # image = Image.new('RGB', (500, 500), color='red')
    except Exception as e:
        print(f"Error loading image {image_path}: {e}")
        continue
    
    # Construct the input messages.
    # Here the prompt is built using the special token <|image|> that mPLUG expects,
    # followed by your question. The second message is left empty for the assistant.

    messages = [
    {

      "role": "user",
      "content": [
          {"type": "text", "text": f"only qnswer the question as short as possible. dont add additional words. {question}"},
          {"type": "image"},
        ],
    },
    ]
    prompt = processor.apply_chat_template(messages, add_generation_prompt=True)
    # Use the processor to convert messages and images to model inputs.
    inputs = processor(images=image, text=prompt, return_tensors='pt').to(0, torch.float16)
    inputs.to('cuda')
    
    # The output is assumed to be a list; here we get the first result.
    output = model.generate(**inputs, max_new_tokens=50, do_sample=False)
    answer = processor.decode(output[0][2:], skip_special_tokens=True)
    generated_answers.append(answer)
    # Display the result.
    print("--------------------------------------------------")
    print(f"Image: {image_path}")
    print(f"Question: {question}")
    print(f"Generated Answer: {answer}")
    print(f"Ground Truth Answer: {gt_answer}")
    print("--------------------------------------------------\n")

# Add the new column to the DataFrame
df['generated_answer'] = generated_answers

# Optionally, save the DataFrame to a CSV file for later use
# df.to_csv('docvqa_generated_answers.csv', index=False)
display(df.head(5))

--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/pybv0228_81.png
Question: What is the ‘actual’ value per 1000, during the year 1975?
Generated Answer: ER:  
only qnswer the question as short as possible. dont add additional words. What is the ‘actual’ value per 1000, during the year 1975? ASSISTANT: 1.0
Ground Truth Answer: ['0.28']
--------------------------------------------------

--------------------------------------------------
Image: /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png
Question: What is name of university?
Generated Answer: ER:  
only qnswer the question as short as possible. dont add additional words. What is name of university? ASSISTANT: Unknown
Ground Truth Answer: ['university of california', 'University of California', 'university of california, san diego']
--------------------------------------------------

------------------------------------------

questionId                                                    question  \
0       49153  What is the ‘actual’ value per 1000, during the year 1975?   
1       24580                                 What is name of university?   
2       57349                            What is the name of the company?   
3       24581                           Where is the university located ?   
4       24582                               To whom is the document sent?   

        question_types  \
0     [figure/diagram]   
1             [others]   
2             [layout]   
3             [others]   
4  [handwritten, form]   

                                                                                 image  \
0  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/pybv0228_81.png   
1   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   
2  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_22.png   
3   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   
4   /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/nkbl0226_1.png   

   docId ucsf_document_id ucsf_document_page_no  \
0  14465         pybv0228                    81   
1   7027         nkbl0226                     1   
2   4733         snbx0223                    22   
3   7027         nkbl0226                     1   
4   7027         nkbl0226                     1   

                                                                                     answers  \
0                                                                                     [0.28]   
1  [university of california, University of California, university of california, san diego]   
2                                                                 [itc limited, ITC Limited]   
3                                                                     [san diego, San Diego]   
4                                                                                     [Paul]   

  data_split  \
0        val   
1        val   
2        val   
3        val   
4        val   

                                                                                                                                             generated_answer  
0  ER:  \nonly qnswer the question as short as possible. dont add additional words. What is the ‘actual’ value per 1000, during the year 1975? ASSISTANT: 1.0  
1                             ER:  \nonly qnswer the question as short as possible. dont add additional words. What is name of university? ASSISTANT: Unknown  
2                            ER:  \nonly qnswer the question as short as possible. dont add additional words. What is the name of the company? ASSISTANT: Tcc  
3                       ER:  \nonly qnswer the question as short as possible. dont add additional words. Where is the university located ? ASSISTANT: Nowhere  
4                        ER:  \nonly qnswer the question as short as possible. dont add additional words. To whom is the document sent? ASSISTANT: Ms. Wilson

In [12]:
df['generated_answer_cleaned'] = df['generated_answer'].apply(
    lambda s: s.split("ASSISTANT:")[-1].strip() if "ASSISTANT:" in s else s.strip()
)

In [13]:
import Levenshtein

def normalized_levenshtein_similarity(s1, s2):
    # If the input is a list, join its elements into a string.
    if isinstance(s1, list):
        s1 = " ".join(map(str, s1))
    if isinstance(s2, list):
        s2 = " ".join(map(str, s2))
        
    # Convert to string, lowercase, and remove surrounding whitespace.
    s1 = str(s1).lower().strip()
    s2 = str(s2).lower().strip()
    
    dist = Levenshtein.distance(s1, s2)
    max_len = max(len(s1), len(s2))
    if max_len == 0:
        return 1.0
    return 1 - (dist / max_len)

# Function to compute the similarity for a single row
def row_similarity(row):
    # Assume row['answers'] is a list of ground-truth strings
    ground_truths = row['answers']
    generated = row['generated_answer_cleaned']
    # Compute similarity with each ground truth answer
    similarities = [normalized_levenshtein_similarity(gt, generated) for gt in ground_truths]
    # We take the maximum similarity (best match) as the score for that row.
    return max(similarities) if similarities else 0.0


# Compute similarity for each row
df["similarity"] = df.apply(row_similarity, axis=1)

# Calculate the average similarity (ANSL)
ansl_accuracy = df["similarity"].mean()

print("Row similarities:")
print(df[["answers", "generated_answer", "similarity"]])
print("Average Normalized Levenshtein Similarity (ANSL):", ansl_accuracy)

Row similarities:
                                                                                                                        answers  \
0                                                                                                                        [0.28]   
1                                     [university of california, University of California, university of california, san diego]   
2                                                                                                    [itc limited, ITC Limited]   
3                                                                                                        [san diego, San Diego]   
4                                                                                                                        [Paul]   
...                                                                                                                         ...   
5344                                                             

In [14]:
df[df["similarity"]<0.5].iloc[20:40].head(20)

questionId  \
22       57376   
23       49187   
24       16424   
25       57386   
26       57387   
29       16430   
30       57391   
31       57395   
34       57402   
35       57403   
36       57404   
38       57407   
39       16447   
40       57409   
43       57411   
44       57413   
45       57414   
46       57415   
47       57416   
48       57417   

                                                                                       question  \
22                                  What is the % of raw material imported in the current year?   
23                                                 What time is “introductory remarks” session?   
24                                              Why Taco Bell's strong consumer base decreased?   
25                                 What is the % of raw material imported in the previous year?   
26                          What is the % value of indigenous raw material in the current year?   
29                                              What is the page no mentioned in this document?   
30                                                             What is the name of the company?   
31                                        Where is the ITC Life Sciences and Technology Centre?   
34                                  Who was the director having the highest number of options ?   
35                                               What is the no. of options held by S. H. Khan?   
36                                  What is the no. of Ordinary shares held by Y. C. Deveshwar?   
38                                         What is the no. of Ordinary shares held by N. Anand?   
39  What percentage of non-smokers feel the need to restore romance and mystery to modern life?   
40                                                             What is the name of the company?   
43                                     How many 'energetic and popular brands' has ITC created?   
44                                          Name the 4 significant personal care brands of ITC?   
45                                         What are the 2 educational/stationary brands of ITC?   
46                                            What are the 2 lifestyle & apparel brands of ITC?   
47                                                 What is the name of the ITC Agarbatti brand?   
48                                                     What is the name of ITC's matches brand?   

   question_types  \
22         [form]   
23   [table/list]   
24    [free_text]   
25         [form]   
26         [form]   
29       [layout]   
30       [layout]   
31    [free_text]   
34   [table/list]   
35   [table/list]   
36   [table/list]   
38   [table/list]   
39   [table/list]   
40       [layout]   
43    [free_text]   
44    [free_text]   
45    [free_text]   
46    [free_text]   
47    [free_text]   
48    [free_text]   

                                                                                  image  \
22  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/ylvj0223_21.png   
23  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/txpp0227_10.png   
24  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/hsyn0081_31.png   
25  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/ylvj0223_21.png   
26  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/ylvj0223_21.png   
29  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/hsyn0081_31.png   
30  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_14.png   
31  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_14.png   
34  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_42.png   
35  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_42.png   
36  /home/cheng-ubuntu/Documents/ift6765/project/Images/spdocvqa_images/snbx0223_42.png   
38  /home/c